# Day 10 - 3D movies!  VR capabilties!  Woo!

### Topics

 1. Reading in Kepler-11 simulation data & looking at its mass & radii in planets with our NASA database
 1. Download the "generic planet files"
    * by hand
    * with wget
    * ~~with a user-defined function~~
 1. Making realistic planetary systems
 1. BACK TO SLIDES FOR 3D MOVIES INTRO
 1. 3D movies in Sketchfab with a .timeframe file

Let's import our usual things:

In [1]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import ipywidgets

And some user-defined functions to help us parse this data (making sure we have the hermite_library.py file in our directory):

In [2]:
from hermite_library import read_hermite_solution_from_file

## Reading in Kepler-11 simulation data & looking at its mass & radii in planets with our NASA database

Let's import a planet simulation to work with, again assuming the `data` directory containing our simulation files is in the same directory as this notebook:

In [3]:
planet_file = 'data/Kepler-11-savedSim.txt'

t_h, E_h, r_h, v_h = read_hermite_solution_from_file(planet_file)

Before making any visualizations of this, we'll want to get a sense of what the planets in this system look like.  Let's print out some important things -- mass & radii -- of each of these planets by looking back at our planetary database:

In [4]:
planets = pd.read_csv('https://raw.githubusercontent.com/jnaiman/csci-p-14110_su2020/master/lesson08/planets_2020.06.22_10.10.17.csv', 
                      comment="#")

Let's grab some info about this particular planetary system:

In [5]:
#for planet in planets['pl_hostname']:
#    if 'Kepler' in planet:
#        print(planet)

planets.loc[planets['pl_hostname'] == 'Kepler-11']

rowid pl_hostname pl_letter      pl_name pl_discmethod  pl_controvflag  \
1546   1547   Kepler-11         b  Kepler-11 b       Transit               0   
1547   1548   Kepler-11         c  Kepler-11 c       Transit               0   
1548   1549   Kepler-11         d  Kepler-11 d       Transit               0   
1549   1550   Kepler-11         e  Kepler-11 e       Transit               0   
1550   1551   Kepler-11         f  Kepler-11 f       Transit               0   
1551   1552   Kepler-11         g  Kepler-11 g       Transit               0   

      pl_pnum  pl_orbper  pl_orbpererr1  pl_orbpererr2  ...  st_bmy  \
1546        6    10.3039         0.0006        -0.0010  ...     NaN   
1547        6    13.0241         0.0013        -0.0008  ...     NaN   
1548        6    22.6845         0.0009        -0.0009  ...     NaN   
1549        6    31.9996         0.0008        -0.0012  ...     NaN   
1550        6    46.6888         0.0027        -0.0032  ...     NaN   
1551        6   118.3807         0.0010        -0.0006  ...     NaN   

      st_bmyerr  st_bmylim  st_m1  st_m1err  st_m1lim  st_c1  st_c1err  \
1546        NaN        NaN    NaN       NaN       NaN    NaN       NaN   
1547        NaN        NaN    NaN       NaN       NaN    NaN       NaN   
1548        NaN        NaN    NaN       NaN       NaN    NaN       NaN   
1549        NaN        NaN    NaN       NaN       NaN    NaN       NaN   
1550        NaN        NaN    NaN       NaN       NaN    NaN       NaN   
1551        NaN        NaN    NaN       NaN       NaN    NaN       NaN   

      st_c1lim  st_colorn  
1546       NaN        5.0  
1547       NaN        5.0  
1548       NaN        5.0  
1549       NaN        5.0  
1550       NaN        5.0  
1551       NaN        5.0  

[6 rows x 356 columns]

And let's check out the masses and radii of these objects in particular:

In [6]:
planets.loc[planets['pl_hostname'] == 'Kepler-11', 
            ['pl_hostname', 'pl_letter', 'pl_name', 'pl_bmassj', 'pl_radj']]

pl_hostname pl_letter      pl_name  pl_bmassj  pl_radj
1546   Kepler-11         b  Kepler-11 b      0.006    0.161
1547   Kepler-11         c  Kepler-11 c      0.009    0.256
1548   Kepler-11         d  Kepler-11 d      0.023    0.278
1549   Kepler-11         e  Kepler-11 e      0.025    0.374
1550   Kepler-11         f  Kepler-11 f      0.006    0.222
1551   Kepler-11         g  Kepler-11 g      0.079    0.297

Ok cool.  We'll keep this little table us to be able to look at later when we are making some aesthetic choices about our dataset.

## Download the "generic planet files"

Before we get to making a model of our planetary system in 3D we need some graphical objects to update.  These are file formats associated with 3D models (.obj and .mtl files).

There are a few ways to get this data:

1. We can download it by hand here: <a href="https://github.com/jnaiman/csci-p-14110_su2020/raw/master/lesson10/genericPlanetFiles.zip" download>genericPlanetFiles.zip</a>
   * make sure you copy this file to your local directory (or if it unzips itself you can copy that folder here)
1. We can install a package called "wget" and have it do it for us:

In [7]:
!pip install wget

In [8]:
# import wget
# url = 'https://github.com/jnaiman/csci-p-14110_su2020/raw/master/lesson10/genericPlanetFiles.zip'
# filename = wget.download(url)

And then we can unzip this file to have a working directory from which to build models from:

In [9]:
import zipfile

In [10]:
# path_to_zip_file = './genericPlanetFiles.zip'
generic_dir = './genericPlanetFiles/'

# with zipfile.ZipFile(path_to_zip_file, 'r') as zip_ref:
#     zip_ref.extractall(generic_dir)

We're going to use the `make3dplanets` function that got downloaded with the generic planet files, but we have to tell our system where to look for it by updating our PATH variable:

In [11]:
from sys import path
path.append(generic_dir)

In [12]:
from make3dplanets import make3dplanets

To do the "look at the files" thing inline in windows you can replace "ls" with "dir"

In [13]:
!ls genericPlanetFiles

__pycache__      generic.obj      textureMaps
generic.mtl      make3dplanets.py


Let's first try opening the `generic.obj` + `generic.mtl` files in [the creator3d online viewer](https://www.creators3d.com/online-viewer).

## Making realistic planetary systems

We can see its pretty boring -- just a spherical object without any color or texture.  This is our "generic" planet object that we can size up or down and attach different planet textures to.

To do this we have to pick what sizes and textures we think our planets should be.  Lucky for us, we have that info! Let's look at that table again of info:

In [14]:
planets.loc[planets['pl_hostname'] == 'Kepler-11', 
            ['pl_hostname', 'pl_letter', 'pl_name', 'pl_bmassj', 'pl_radj']]
# note: we are using jupter masses and radii!

pl_hostname pl_letter      pl_name  pl_bmassj  pl_radj
1546   Kepler-11         b  Kepler-11 b      0.006    0.161
1547   Kepler-11         c  Kepler-11 c      0.009    0.256
1548   Kepler-11         d  Kepler-11 d      0.023    0.278
1549   Kepler-11         e  Kepler-11 e      0.025    0.374
1550   Kepler-11         f  Kepler-11 f      0.006    0.222
1551   Kepler-11         g  Kepler-11 g      0.079    0.297

We'll need to input the planet radii so:

In [15]:
planets.loc[planets['pl_hostname'] == 'Kepler-11', ['pl_radj']]

pl_radj
1546    0.161
1547    0.256
1548    0.278
1549    0.374
1550    0.222
1551    0.297

In [16]:
planets.loc[planets['pl_hostname'] == 'Kepler-11', ['pl_radj']].values

array([[0.161],
       [0.256],
       [0.278],
       [0.374],
       [0.222],
       [0.297]])

In [17]:
planets.loc[planets['pl_hostname'] == 'Kepler-11', ['pl_radj']].values.flatten() # formatting

array([0.161, 0.256, 0.278, 0.374, 0.222, 0.297])

In [18]:
radii = planets.loc[planets['pl_hostname'] == 'Kepler-11', ['pl_radj']].values.flatten()

Ok, these are just the radii of our *planets*.  We also need to include the radii of the *star*.

In [19]:
planets.loc[planets['pl_hostname'] == 'Kepler-11', ['st_rad']]

st_rad
1546    1.06
1547    1.06
1548    1.06
1549    1.06
1550    1.06
1551    1.06

Since its of the host star and they are all the same, we can just take one:

In [20]:
planets.loc[planets['pl_hostname'] == 'Kepler-11', ['st_rad']].values[0]

array([1.06])

And now we have to append it to the end of our radii list.  Since we are dealing with numpy arrays, we can use numpy's version of append:

In [21]:
radii = np.append(radii, planets.loc[planets['pl_hostname'] == 'Kepler-11', ['st_rad']].values[0])

In [22]:
radii

array([0.161, 0.256, 0.278, 0.374, 0.222, 0.297, 1.06 ])

Ok neat!  The last thing we need to do is define a directory where we will save all of our planet systems:

In [23]:
out_planet_dir = './outPlanets/' # so in a sub-directory

... and what to call our planetary system:

In [24]:
SystemName = 'kepler11_take1'

Finally, we are going to start with only one timestep, let's start with the zero-th timestep:

In [25]:
Nplot = 0

Put it all together by and us the make planet files!

In [26]:
fname = make3dplanets(SystemName, r_h, radii, out_planet_dir, generic_dir, Nplot=0)

Going to overwrite files in  ./outPlanets/kepler11_take1/
Assuming radii are in Jupiter units except for the last particle which should have solar units, distances in AU... if not things are going to look weird!
no colors/textures specified -- generating random colors!


In [27]:
fname

'kepler11_take1.obj'

This will be the name of the base file.  Let's take a look!

In [28]:
!ls outPlanets

kepler11-movie kepler11_take1


In [29]:
!ls outPlanets/kepler11_take1

kepler11_take1.mtl kepler11_take1.obj


If we upload this to [creator3d.com's online viewer](https://www.creators3d.com/online-viewer) we notice that we don't see anything except the host star!  This is because as we talked about a few days ago its hard to both show planet distances and radii correctly at the same time since the spaces are so huge.  Let's try making our radii artifically bigger, *but only for the planets*:

In [30]:
radii = planets.loc[planets['pl_hostname'] == 'Kepler-11', ['pl_radj']].values.flatten()*100
radii = np.append(radii, planets.loc[planets['pl_hostname'] == 'Kepler-11', ['st_rad']].values[0])
radii

array([16.1 , 25.6 , 27.8 , 37.4 , 22.2 , 29.7 ,  1.06])

and recreate our 3D system:

In [31]:
fname = make3dplanets(SystemName, r_h, radii, out_planet_dir, generic_dir, Nplot=0)

Going to overwrite files in  ./outPlanets/kepler11_take1/
Assuming radii are in Jupiter units except for the last particle which should have solar units, distances in AU... if not things are going to look weird!
no colors/textures specified -- generating random colors!


And now if we reupload to [creator3d.com's online viewer](https://www.creators3d.com/online-viewer) we can see the initial starting positions of our objects much more clearly.

### Adding in textures

So far, we've been letting the 3D planet generator choose the colors for us.  Now we'll pick some textures based on what we think these planets/star look like.

Going back to our table:

In [32]:
planets.loc[planets['pl_hostname'] == 'Kepler-11', 
            ['pl_hostname', 'pl_letter', 'pl_name', 'pl_bmassj', 'pl_radj']]

pl_hostname pl_letter      pl_name  pl_bmassj  pl_radj
1546   Kepler-11         b  Kepler-11 b      0.006    0.161
1547   Kepler-11         c  Kepler-11 c      0.009    0.256
1548   Kepler-11         d  Kepler-11 d      0.023    0.278
1549   Kepler-11         e  Kepler-11 e      0.025    0.374
1550   Kepler-11         f  Kepler-11 f      0.006    0.222
1551   Kepler-11         g  Kepler-11 g      0.079    0.297

Looking at wikipedia we can check out the [relative masses of objects in the solar system in Jupiter masses](https://en.wikipedia.org/wiki/Jupiter_mass#Relative_mass) we see that our objects are between Earth-mass and Neptune mass.  Also, our host star is ~mass of sun, so we'll use the sun texture.  So, let's make a list of textures to associate with each system from the planet system directory:

In [33]:
!ls genericPlanetFiles/textureMaps/

MarsMap_2500x1250.jpg          preview_sun.jpg
earth_1200.jpg                 red_sun.jpg
green_sun.jpg                  saturn_1024.jpg
jupiter_1200.jpg               sun_texture1.jpg
mercury_1024.jpg               uranus_1024.jpg
neptunemap_1000.jpg            venus_surface_texture_1024.jpg
pluto_1024.jpg


In [34]:
planet_textures = ['earth_1200.jpg', # Kepler-11 b
                  'uranus_1024.jpg', # c
                  'uranus_1024.jpg', # d
                  'uranus_1024.jpg', # e
                  'earth_1200.jpg', #f
                  'saturn_1024.jpg', #g
                  'sun_texture1.jpg'] # last one is a sun texture

Recall & make planets again:

In [35]:
fname = make3dplanets(SystemName, r_h, radii, out_planet_dir, generic_dir, texture_file=planet_textures, Nplot=0)

Going to overwrite files in  ./outPlanets/kepler11_take1/
Assuming radii are in Jupiter units except for the last particle which should have solar units, distances in AU... if not things are going to look weird!


Now if we look in our outplanet directory we can see that we have another file with our texture maps:

In [36]:
!ls outPlanets/kepler11_take1/

earth_1200.jpg     kepler11_take1.obj sun_texture1.jpg
kepler11_take1.mtl saturn_1024.jpg    uranus_1024.jpg


Now we can upload all of these files to the creator3d webpage for a quick look.

Now would be a great time to test uploading to Sketchfab and play around with all of the controls!

**DO THIS**

## BACK TO SLIDES FOR 3D MOVIES INTRO

## 3D movies in Sketchfab with a .timeframe file

Now, lets make an array of time steps we want to use.  Let's start with two only and we can increase this as we go to make longer/less choppy movies.  But 2 is good to debug!

In [37]:
Nplots = [5, 100] # make a "movie" with timesteps 5 & 100

Let's call this system differently:

In [38]:
SystemName = 'kepler11-movie'

Now let's make the planet files!   Now, this is a loop and we have to save the delta-t's between each file for outputing to  a ```sketchfab.timeframe``` later.

How much time (in seconds) do we want between these two snapshots?

In [39]:
dt_movie = 0.5 # 1/2 second

Now let's loop over our selected snapshots and save files!

In [40]:
# save dts
time_list = []

for iplot, Nplot in enumerate(Nplots): # fancy way to loop and count at the same time
    fname = make3dplanets(SystemName, r_h, radii, out_planet_dir, 
                          generic_dir, texture_file=planet_textures, 
                          Nplot=Nplot, fnum=iplot, verbose=False) # setting a few extra params
    #print('saving:', fname, iplot)
    # save the time
    time_list.append( str(dt_movie) + ' ' + fname + '\n') # note new-line character

In [41]:
SystemName, out_planet_dir

('kepler11-movie', './outPlanets/')

Finally, we have to save all our times and filenames in the .timeframe file:

In [42]:
time_list

['0.5 kepler11-movie0000.obj\n', '0.5 kepler11-movie0001.obj\n']

In [43]:
timeframe_filename = out_planet_dir+SystemName+'/sketchfab.timeframe'
ftime = open(timeframe_filename,'w')

for tobj in time_list:
    ftime.write(tobj)
    
# close file
ftime.close()

In [44]:
!ls outPlanets/kepler11-movie/

earth_1200.jpg         kepler11-movie0001.obj sun_texture1.jpg
kepler11-movie.mtl     saturn_1024.jpg        uranus_1024.jpg
kepler11-movie0000.obj sketchfab.timeframe


In [45]:
# this is just for me to re-zip things at the end of mods

save_mods = False

if save_mods:
    import os
    import zipfile

    def zipdir(path, ziph):
        # ziph is zipfile handle
        for root, dirs, files in os.walk(path):
            for file in files:
                ziph.write(os.path.join(root, file))

    zipf = zipfile.ZipFile('../genericPlanetFiles.zip', 'w', zipfile.ZIP_DEFLATED)
    zipdir('./genericPlanetFiles', zipf)
    zipf.close()